# Policy Gradient

* http://karpathy.github.io/2016/05/31/rl/
* https://gist.github.com/karpathy/a4166c7fe253700972fcbc77e4ea32c5

## Step 1: Installation and setup for the envionronment



In [ ]:
!apt-get install python-opengl -y
!apt install xvfb -y
!pip install pyvirtualdisplay
!pip install piglet
!pip install -U gym
!pip install -U ale-py

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
E: Unable to locate package python-opengl
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following additional packages will be installed:
  libfontenc1 libxfont2 libxkbfile1 x11-xkb-utils xfonts-base xfonts-encodings xfonts-utils
  xserver-common
The following NEW packages will be installed:
  libfontenc1 libxfont2 libxkbfile1 x11-xkb-utils xfonts-base xfonts-encodings xfonts-utils
  xserver-common xvfb
0 upgraded, 9 newly installed, 0 to remove and 9 not upgraded.
Need to get 7,814 kB of archives.
After this operation, 11.9 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/main amd64 libfontenc1 amd64 1:1.1.4-1build3 [14.7 kB]
Get:2 http://archive.ubuntu.com/ubuntu jammy/main amd64 libxfont2 amd64 1:2.0.5-1build1 [94.5 kB]
Get:3 http://archive.ubuntu.com/ubuntu jammy/main amd64 libxkbfile1 amd64 1:1.

In [ ]:
!wget http://www.atarimania.com/roms/Roms.rar
!unrar x Roms.rar -y
!mv "ROMS/Video Olympics - Pong Sports (Paddle) (1977) (Atari, Joe Decuir - Sears) (CX2621 - 99806, 6-99806, 49-75104) ~.bin" "ROMS/pong.bin"
!ale-import-roms ROMS/

流式输出内容被截断，只能显示最后 5000 行内容。
Extracting  HC ROMS/BY ALPHABET/A-G/Crash Dive.bin                        43%  OK 
Extracting  HC ROMS/BY ALPHABET/A-G/Crazy Climber.bin                     43%  OK 
Extracting  HC ROMS/BY ALPHABET/A-G/Cross Force.bin                       44%  OK 
Extracting  HC ROMS/BY ALPHABET/A-G/Crossbow.bin                          44%  OK 
Extracting  HC ROMS/BY ALPHABET/A-G/Crypts of Chaos.bin                   44%  OK 
Extracting  HC ROMS/BY ALPHABET/A-G/Crystal Castles.bin                   44%  OK 
Extracting  HC ROMS/BY ALPHABET/A-G/Cubicolor (Prototype).bin             44%  OK 
Extracting  HC ROMS/BY ALPHABET/A-G/Custer's Revenge.bin                  44%  OK 
Extracting  HC ROMS/BY ALPHABET/A-G/Dancing Plate (PAL).bin               44%  OK 
Extracting  HC ROMS/BY ALPHABET/A-G/Dark Cavern.bin                       44%  OK 
Extracting  HC ROMS/BY ALPHABET/A-G/Dark Chambers.bin

In [ ]:
from ale_py import ALEInterface
from ale_py.roms import Pong

ale = ALEInterface()
ale.loadROM(Pong)

In [ ]:
from pyvirtualdisplay import Display
display = Display(visible=0, size=(1400, 900))
display.start()

In [ ]:
%matplotlib inline
from matplotlib import animation
import matplotlib.pyplot as plt
from IPython.display import display, HTML

def display_frames_as_gif(frames):
    """
    Displays a list of frames as a gif, with controls
    """
    plt.figure(figsize=(frames[0].shape[1] / 72.0, frames[0].shape[0] / 72.0), dpi = 144)
    patch = plt.imshow(frames[0])
    plt.axis('off')

    def animate(i):
        patch.set_data(frames[i])

    anim = animation.FuncAnimation(plt.gcf(), animate, frames = len(frames), interval=50)
    plt.close(anim._fig)
    display(HTML(anim.to_jshtml()))

## Step 2: Setting up the gym environment


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import gym
# env = gym.make('ALE/Pong-v5', render_mode='rgb_array')
env = gym.make('PongDeterministic-v4', render_mode='rgb_array')

In [ ]:
env.unwrapped.get_action_meanings()

['NOOP', 'FIRE', 'RIGHT', 'LEFT', 'RIGHTFIRE', 'LEFTFIRE']

In [ ]:
env.action_space

Discrete(6)

In [ ]:
# Run a demo of the environment
observation = env.reset()
cumulated_reward = 0

frames = []
for t in range(1000):
#     print(observation)
    frames.append(env.render())
    # very stupid agent, just makes a random action within the allowd action space
    action = env.action_space.sample()
#     print("Action: {}".format(t+1))
    observation, reward, done, truncated, info = env.step(action)
#     print(reward)
    cumulated_reward += reward
    if done:
        print("Episode finished after {} timesteps, accumulated reward = {}".format(t+1, cumulated_reward))
        break
print("Episode finished without success, accumulated reward = {}".format(cumulated_reward))

env.close()

/usr/local/lib/python3.10/dist-packages/gym/utils/passive_env_checker.py:289: UserWarning: WARN: No render fps was declared in the environment (env.metadata['render_fps'] is None or not defined), rendering may occur at inconsistent fps.
  logger.warn(


Episode finished after 871 timesteps, accumulated reward = -20.0
Episode finished without success, accumulated reward = -20.0


In [ ]:
display_frames_as_gif(frames)

## Step 3: Policy Gradient from Scratch

In [ ]:
def sigmoid(x):
  return 1.0 / (1.0 + np.exp(-x)) # sigmoid "squashing" function to interval [0,1]

def prepro(I):
  """ prepro 210x160x3 uint8 frame into 6400 (80x80) 1D float vector """
  I = I[35:195] # crop
  I = I[::2,::2,0] # downsample by factor of 2
  I[I == 144] = 0 # erase background (background type 1)
  I[I == 109] = 0 # erase background (background type 2)
  I[I != 0] = 1 # everything else (paddles, ball) just set to 1
  return I.astype(float).ravel()


In [ ]:
import numpy as np

In [ ]:
def discount_rewards(r):
  """ take 1D float array of rewards and compute discounted reward """
  discounted_r = np.zeros_like(r)
  running_add = 0
  for t in reversed(range(0, r.size)):
    if r[t] != 0: running_add = 0 # reset the sum, since this was a game boundary (pong specific!)
    running_add = running_add * gamma + r[t]
    discounted_r[t] = running_add
  return discounted_r

In [ ]:
def policy_forward(x):
  h = np.dot(model['W1'], x)
  h[h<0] = 0 # ReLU nonlinearity
  h1 = np.dot(model['W3'], h)
  logp = np.dot(model['W2'], h1)
  p = sigmoid(logp)
  return p, h1, h # return probability of taking action 2, and hidden state

In [ ]:
def policy_backward(epx, eph, eph1, epdlogp):
  """ backward pass. (eph is array of intermediate hidden states) """
  dW2 = np.dot(eph1.T, epdlogp).ravel()
  dh1 = np.outer(epdlogp, model['W2'])
  dW3 = np.dot(dh1.T, eph1)
  dh = np.dot(dh1, model['W3'])
  dh[eph <= 0] = 0 # backpro prelu
  dW1 = np.dot(dh.T, epx)
  return {'W1':dW1, 'W2':dW2, 'W3':dW3}

In [ ]:
def model_step(model, observation, prev_x):
  # preprocess the observation, set input to network to be difference image

  # obs_arr = np.array(observation)
  # cur_x = prepro(obs_arr)


  cur_x = prepro(observation)
  x = cur_x - prev_x if prev_x is not None else np.zeros(D)
  prev_x = cur_x

  # forward the policy network and sample an action from the returned probability
  aprob, _, _ = policy_forward(x)
  action = 2 if aprob >= 0.5 else 3 # roll the dice!

  return action, prev_x

In [ ]:
def play_game(env, model):
  observation = env.reset()

  frames = []
  cumulated_reward = 0

  prev_x = None # used in computing the difference frame

  for t in range(1000):
      frames.append(env.render())
      action, prev_x = model_step(model, observation, prev_x)
      observation, reward, done, truncated, info = env.step(action)
      cumulated_reward += reward
      if done:
          print("Episode finished after {} timesteps, accumulated reward = {}".format(t+1, cumulated_reward))
          break
  print("Episode finished without success, accumulated reward = {}".format(cumulated_reward))
  env.close()
  display_frames_as_gif(frames)

In [ ]:
import pickle
# model = pickle.load(open('/content/drive/MyDrive/Colab Notebooks/COMP7409 Machine learning in trading and finance/data/model.pkl', 'rb'))

In [ ]:
def train_model(env, model, total_episodes = 100):
  hist = []
  observation = env.reset()
  observation = observation[0]
  prev_x = None # used in computing the difference frame
  xs,hs,h1s,dlogps,drs = [],[],[],[],[]
  running_reward = None
  reward_sum = 0
  episode_number = 0

  while True:
    # preprocess the observation, set input to network to be difference image

    # obs_arr = np.array(observation)
    # cur_x = prepro(obs_arr)

    cur_x = prepro(observation)
    x = cur_x - prev_x if prev_x is not None else np.zeros(D)
    prev_x = cur_x

    # forward the policy network and sample an action from the returned probability
    aprob, h1, h = policy_forward(x)
    action = 2 if np.random.uniform() < aprob else 3 # roll the dice!

    # record various intermediates (needed later for backprop)
    xs.append(x) # observation
    hs.append(h) # hidden state
    h1s.append(h1) # hidden state
    y = 1 if action == 2 else 0 # a "fake label"
    dlogps.append(y - aprob) # grad that encourages the action that was taken to be taken (see http://cs231n.github.io/neural-networks-2/#losses if confused)

    # step the environment and get new measurements
    observation, reward, done, truncated, info = env.step(action)
    reward_sum += reward

    drs.append(reward) # record reward (has to be done after we call step() to get reward for previous action)

    if done: # an episode finished
      episode_number += 1

      # stack together all inputs, hidden states, action gradients, and rewards for this episode
      epx = np.vstack(xs)
      eph = np.vstack(hs)
      eph1 = np.vstack(h1s)
      epdlogp = np.vstack(dlogps)
      epr = np.vstack(drs)
      xs,hs,h1s,dlogps,drs = [],[],[],[],[] # reset array memory

      # compute the discounted reward backwards through time
      discounted_epr = discount_rewards(epr)
      # standardize the rewards to be unit normal (helps control the gradient estimator variance)
      discounted_epr -= np.mean(discounted_epr)
      discounted_epr /= np.std(discounted_epr)

      epdlogp *= discounted_epr # modulate the gradient with advantage (PG magic happens right here.)
      grad = policy_backward(epx, eph, eph1, epdlogp)
      for k in model: grad_buffer[k] += grad[k] # accumulate grad over batch

      # perform rmsprop parameter update every batch_size episodes
      if episode_number % batch_size == 0:
        for k,v in model.items():
          g = grad_buffer[k] # gradient
          rmsprop_cache[k] = decay_rate * rmsprop_cache[k] + (1 - decay_rate) * g**2
          model[k] += learning_rate * g / (np.sqrt(rmsprop_cache[k]) + 1e-5)
          grad_buffer[k] = np.zeros_like(v) # reset batch gradient buffer

      # boring book-keeping
      running_reward = reward_sum if running_reward is None else running_reward * 0.99 + reward_sum * 0.01
      hist.append((episode_number, reward_sum, running_reward))
      print ('resetting env. episode %f, reward total was %f. running mean: %f' % (episode_number, reward_sum, running_reward))
      if episode_number % 100 == 0: pickle.dump(model, open(save_file, 'wb'))

      reward_sum = 0
      observation = env.reset() # reset env
      observation = observation[0]
      prev_x = None
      if episode_number == total_episodes:
        return hist

    # if reward != 0: # Pong has either +1 or -1 reward exactly when game ends.
    #   print('ep {}: game finished, reward: {}'.format(episode_number, reward) + ('' if reward == -1 else ' !!!!!!!!'))

In [ ]:
import numpy as np

# model initialization
H = 200 # number of hidden layer neurons
D = 80 * 80 # input dimensionality: 80x80 grid

# resume = False  # resume from previous checkpoint?
# test = False  # test mode, turn off epsilon-greedy and render the scene

resume = True  # resume from previous checkpoint?
test = True  # test mode, turn off epsilon-greedy and render the scene

# save_file = 'pong_model_bolei.p'
save_file = '/content/drive/MyDrive/Colab Notebooks/COMP7409 Machine learning in trading and finance/data/model.p'

if resume:
    model = pickle.load(open(save_file, 'rb'))
else:
    model = {}
    model['W1'] = np.random.randn(H,D) / np.sqrt(D) # "Xavier" initialization
    model['W3'] = np.random.randn(H,H) / np.sqrt(H)
    model['W2'] = np.random.randn(H) / np.sqrt(H)



In [ ]:
if test == True:
    render = True
else:
    render = False

In [ ]:
if render:
    env = gym.make('PongDeterministic-v4', render_mode='rgb_array')
else:
    env = gym.make('PongDeterministic-v4')

In [ ]:
# hyperparameters
batch_size = 10 # every how many episodes to do a param update?
# learning_rate = 1e-4
learning_rate = 1e-3

gamma = 0.99 # discount factor for reward
decay_rate = 0.99 # decay factor for RMSProp leaky sum of grad^2

grad_buffer = { k : np.zeros_like(v) for k,v in model.items() } # update buffers that add up gradients over a batch
rmsprop_cache = { k : np.zeros_like(v) for k,v in model.items() } # rmsprop memory

In [ ]:
%time hist1 = train_model(env, model, total_episodes=500)

In [ ]:
%time hist2 = train_model(env, model, total_episodes=1)

# Test